# Permutations

Marc Lorenzi

31 mars 2023

In [ ]:
import random
import math
import matplotlib.pyplot as plt

## 1. Introduction

### 1.1 Permutations et Python

Dans tout ce notebook, $n$ désigne un entier naturel. On note $\mathfrak S_n=\mathfrak S([|0,n-1|])$ l'ensemble des permutations de l'ensemble $[|0,n-1|]$.

On représente en Python une permutation $\sigma\in\mathfrak S_n$ par la liste $[\sigma(0),\ldots,\sigma(n-1)]$.

La fonction `print_perm` permet d'afficher de façon agréable une permutation $s$.

In [ ]:
def print_perm(s):
    n = len(s)
    ln = n * '+---' + '+'
    print(ln)
    for k in range(n):
        print('|%2d ' % k, end='')
    print('|')
    print(ln)
    for k in range(n):
        print('|%2d ' % s[k], end='')
    print('|')
    print(ln)    

In [ ]:
print_perm([7, 1, 2, 4, 3, 6, 5, 8, 10, 9, 0])

### 1.2 Permutations aléatoires

Il sera bien utile d'avoir pour nos tests une fonction qui renvoie une permutation « aléatoire ». La fonction `random_perm` prend en paramètre un entier $n$ et renvoie une permutation de $\mathfrak S_n$. L'algorithme utilisé est *l'algorithme de Fisher-Yates*. 

Munissons $\mathfrak S_n$ de la probabilité uniforme $\mathbb P$. La fonction `random_perm` peut être vue comme une variable aléatoire $X$ à valeurs dans $\mathfrak S_n$. On peut montrer (nous ne le ferons pas ici) que pour toute permutation $\sigma\in\mathfrak S_n$, on a $\mathbb P(X=\sigma)=\frac 1 {n!}$. Comme le cardinal de $\mathfrak S_n$ est $|\mathfrak S_n|=\frac 1{n!}$, la variable aléatoire $X$ suit une loi uniforme.

In [ ]:
def random_perm(n):
    s = list(range(n))
    for i in range(n - 1, -1, -1):
        j = random.randint(i, n - 1)
        s[i], s[j] = s[j], s[i]
    return s

In [ ]:
s = random_perm(15)
print_perm(s)

## 2. Opérations sur les permutations

$(\mathfrak S_n,\circ)$ est un groupe pour la composition des applications.

### 2.1 Élément neutre

La fonction `id` renvoie la permutation identité, neutre de $\mathfrak S_n$.

In [ ]:
def id(n):
    return list(range(n))

In [ ]:
print_perm(id(10))

### 2.2 Produit

La fonction `produit` renvoie la composée des deux permutations $s_1$ et $s_2$, supposées de même taille.

In [ ]:
def produit(s1, s2):
    n = len(s1)
    return [s1[s2[k]] for k in range(n)]

In [ ]:
print_perm(produit([1, 4, 0, 3, 2], [4, 0, 1, 3, 2]))

In [ ]:
s1 = random_perm(10)
s2 = random_perm(10)
print_perm(s1)
print_perm(s2)
print_perm(produit(s1, s2))
print_perm(produit(s2, s1))

### 2.3 Inverse

La fonction `inverse` renvoie l'inverse de la permutation $s$.

In [ ]:
def inverse(s):
    n = len(s)
    s1 = n * [None]
    for k in range(n):
        s1[s[k]] = k
    return s1

In [ ]:
print_perm(inverse([5,3,1,2,0,4]))

Le produit d'une permutation et de son inverse est égal à $id$. Faisons un petit test.

In [ ]:
s1 = random_perm(15)
s2 = inverse(s1)
print_perm(s1)
print_perm(s2)
print(produit(s1, s2) == id(15), produit(s2, s1) == id(15))

### 2.4 Puissances

Comme dans tous les groupes, on dispose dans $\mathfrak S_n$ de la notion de puissance.

La fonction `puissance` prend en paramètre une permutation $s$ et un entier relatif $n$. Elle renvoie $s^n$. Elle utilise l'algorithme d'exponentiation rapide.

In [ ]:
def puissance(s, n):
    if n < 0: 
        s = inverse(s)
        n = -n
    z = list(range(len(s)))
    while n > 0:
        if n % 2 == 1:
            z = produit(z, s)
        s = produit(s, s)
        n = n // 2
    return z

In [ ]:
s = random_perm(15)
print_perm(puissance(s, 123456789101112))

In [ ]:
s = random_perm(15)
print_perm(puissance(s, -123456789101112))

In [ ]:
s = random_perm(15)
print_perm(produit(puissance(s, 123456789101112), puissance(s, -123456789101112)))

## 3. Décomposition en produit de cycles de supports disjoints

Toute permutation se décompose en produit de cycles de supports disjoints. La décomposition est unique à l'ordre près des facteurs.

On représente en Python un cycle $\gamma$ de longueur $k\ge 2$ par une liste $[a_0\ldots a_{k-1}]$, où $\gamma(a_0)=a_1$, $\gamma(a_1)=a_2$, $\ldots\gamma(a_{k-1})=a_0$.

### 3.1 Orbites

La fonction `orbite` prend en paramètres une permutation $s$ et un entier $x$. Elle renvoie sous forme de liste l'orbite de $x$ suivant $s$, parcourue dans l'ordre. Le troisième paramètre, $e$, est optionnel. Si $e$ est différent de `None`, c'est un ensemble auquel on retire au fur et à mesure les éléments de l'orbite de $x$.

In [ ]:
def orbite(s, x, e=None):
    c = [x]
    y = s[x]
    while y != x:
        c.append(y)
        if e != None: e.remove(y)
        y = s[y]
    return c

In [ ]:
s = random_perm(15)
c = orbite(s, 0)
print_perm(s)
print(c)

### 3.2 Décomposition en produit de cycles

La fonction `vers_cycles` prend en paramètre une permutation $\sigma$ et renvoie une liste de cycles dont le produit est $\sigma$.

In [ ]:
def vers_cycles(s):
    n = len(s)
    cs = []
    e = set(range(n))
    while len(e) != 0:
        x = e.pop()
        c = orbite(s, x, e)
        if len(c) != 1: cs.append(c)
    return cs

In [ ]:
s = random_perm(15)
cs = vers_cycles(s)
print_perm(s)
print(cs)

### 3.3 Recomposition

La fonction `vers_permut` effectue l'opération inverse de `vers_cycles`. Elle prend en paramètre une liste de cycles (supposés de supports disjoints) et renvoie leur produit.

In [ ]:
def vers_permut(cs, n):
    s = list(range(n))
    for c in cs:
        lc = len(c)
        for i in range(lc - 1):
            s[c[i]] = c[i + 1]
        s[c[lc - 1]] = c[0]
    return s    

Vérifions que `vers_permut` est bien inverse à gauche de `vers_cycles`.

In [ ]:
s1 = random_perm(1000)
cs = vers_cycles(s1)
s2 = vers_permut(cs, 1000)
print(s1 == s2)

### 3.4 Nombre d'orbites

La fonction `nombre_orbites` prend en paramètre un permutation $s$. Elle renvoie un triplet $(n_1, n_2, n_3)$ où

- $n_1$ est le nombre d'orbites de $s$ non réduites à un point
- $n_2$ est le nombre de points fixes de $s$
- $n_3 = n_1 + n_2$ est le nombre total d'orbites.

In [ ]:
def nombre_orbites(s):
    cs = vers_cycles(s)
    n1 = len(cs)
    n2 = len(s)
    for c in cs: n2 = n2 - len(c)
    return (n1, n2, n1 + n2)

In [ ]:
s = random_perm(15)
print_perm(s)
print(vers_cycles(s))
print(nombre_orbites(s))

## 4. Quelques statistiques

Nous allons dans cette section nous livrer à quelques statistiques concernant les orbites et les points fixes d'une permutation. Commençons par quelque chose de simple.

### 4.1 Points fixes

Combien une permutation possède-t-elle de points fixes ?

In [ ]:
def nombre_points_fixes(s):
    return nombre_orbites(s)[1]

La fonction `stats_points_fixes` renvoie une estimation du nombre « moyen » de points fixes d'une permutation de $\mathfrak S_n$.

In [ ]:
def stats_points_fixes(n, N=1000):
    a = 0.
    for k in range(N):
        s = random_perm(n)
        a = a + nombre_points_fixes(s)
    return a / N

In [ ]:
stats_points_fixes(100)

**Proposition vague.** Le nombre moyen de points fixes d'une permutation de $\mathfrak S_n$ est égal à 1.

Rendons tout d'abord la proposition moins vague. Munissons $\mathfrak S_n$ de la probabilité uniforme $\mathbb P$. Pour $i\in[|0,n-1|]$, soit $X_i:\mathfrak S_n\longrightarrow\mathbb R$ définie par $X_i(\sigma)=1$ si $\sigma(i)=i$ et $X_i(\sigma)=0$ sinon. Posons enfin

$$X=\sum_{i=0}^{n-1}X_i$$

Pour toute permutation $\sigma\in\mathfrak S_n$, $X(\sigma)$ est le nombre de points fixes de $\sigma$.

**Proposition.** L'espérance de la variable aléatoire $X$ est $E(X)=1$.

**Démonstration.** Pour tout $i\in[|0,n-1|]$, $X_i$ suit une loi de Bernoulli. Le paramètre de cette loi est

$$p_i=\mathbb P(X_i=1)$$

Considérons l'événement $A_i=\{X_i=1\}$. On a

$$A_i=\{\sigma\in\mathfrak S_n:\sigma(i)=i\}$$

On vérifie facilement que l'ensemble $A_i$ est en bijection avec $\mathfrak S_{n-1}$. De là,

$$p_i=\mathbb P(A_i)=\frac{|A_i|}{n!}=\frac{(n-1)!}{n!}=\frac 1 n$$

Ainsi, $E(X_i)=\frac 1 n$. Il ne reste plus qu'à utiliser la linéarité de l'espérance.

$$E(X)=\sum_{i=0}^{n-1}E(X_i)=1$$

### 4.2 Nombre d'orbites

Généralisons un peu. Soit $k\in[|1,n|]$. Combien une permutation $\sigma\in\mathfrak S_n$ possède-t-elle d'orbites de cardinal $k$ ?

Notons $C_k(\sigma)$ le nombre d'orbites selon $\sigma$ qui sont de cardinal $k$.

**Proposition.** On a

$$\sum_{\sigma\in\mathfrak S_n}kC_k(\sigma)=n!$$

**Démonstration.** Considérons l'ensemble

$$A=\{(a,\sigma):\sigma\in\mathfrak S_n, a\text{ appartient à une orbite de cardinal }k\text{ suivant }\sigma\}$$

Soit $\sigma\in\mathfrak S_n$. La permutation $\sigma$ a $C_k(\sigma)$ orbites de cardinal $k$, et dans chacune de ces orbites il y a $k$ points. Ainsi,

$$|A|=\sum_{\sigma\in\mathfrak S_n}kC_k(\sigma)$$

Calculons le cardinal de $A$ d'une autre façon. Soit $a\in[|0,n-1|]$. Pour créer une permutation pour laquelle $a$ est dans une orbite de cardinal $k$ :

- On choisit un ensemble $B\subseteq [|0,n-1|]$ de cardinal $k-1$ (l'orbite sera $B\cup\{a\}$) : $\binom {n-1}{k-1}$ possibilités. 
- On choisit un cycle de longueur $k$ dont le support est $B\cup\{a\}$ : $(k-1)!$ possibilités.
- On choisit une permutation des $n-k$ entiers restants : $(n-k)!$ possibilités.

Le nombre de permutations pour lesquelles $a$ est dans une orbite de cardinal $k$ est donc

$$\binom {n-1}{k-1}(k-1)!(n-k)!=(n-1)!$$

De là,

$$|A|=\sum_{a=0}^{n-1}(n-1)!=n(n-1)!=n!$$

**Proposition.** Pour tout $k\in[|1,n|]$, $E(C_k)=\frac 1 k$.

**Démonstration.** On a

$$E(C_k)=\frac 1{n!}\sum_{\sigma\in\mathfrak S_n}C_k(\sigma)=\frac 1k$$

Pour $k=1$, nous retrouvons que l'espérance du nombre de points fixes d'une permutation est égal à 1.

Maintenant, quel est le nombre d'orbites d'une permutation $\sigma\in\mathfrak S_n$ ? Notons ce nombre $\Omega(\sigma)$. On a évidemment

$$\Omega(\sigma)=\sum_{k=1}^n C_k(\sigma)$$

De là, par la linéarité de l'espérance,

$$E(\Omega)=\sum_{k=1}^n E(C_k)=\sum_{k=1}^n \frac 1 k=H_n$$

où $H_n$ est le $n$ième nombre harmonique.

In [ ]:
def H(n):
    s = 0
    for k in range(1, n + 1):
        s += 1 / k
    return s

In [ ]:
for n in range(1, 11):
    print(n, H(n))

La fonction `stats_orbites` renvoie une liste $S$ de longueur $n+1$. Pour $0\le k\le n$, $S[k]$ est une estimation de $E(C_k)$. Bien entendu, $S[0]=0$.

In [ ]:
def stats_orbites(n, N=1000):
    S = (n + 1) * [0]
    for k in range(N):
        s = random_perm(n)
        cs = vers_cycles(s)
        for c in cs:
            l = len(c)
            S[l] = S[l] + 1
        S[1] += nombre_points_fixes(s)
    for k in range(n + 1):
        S[k] = S[k] / N
    return S

In [ ]:
print(stats_orbites(20))

In [ ]:
plt.rcParams['figure.figsize'] = (8, 3)

Ci-dessous, en noir le nombre « moyen » d'orbites en fonction de $n$. En rouge, la « courbe » de la suite $n\longmapsto H_n$.

In [ ]:
ks = range(1, 100, 4)
s = [sum(stats_orbites(k, 1000)) for k in ks]
lg = [H(k) for k in range(1, 100)]
plt.plot(lg, 'r')
plt.plot(ks, s, 'ok', ms=3)
plt.grid()

## 5. Signature

La signature de la permutation $\sigma\in\mathfrak S_n$ est $\varepsilon(\sigma)=(-1)^{n-m}$ où $m$ est le nombre d'orbites selon $\sigma$. La fonction $\varepsilon:\mathfrak S_n\longrightarrow\{-1,1\}$ est un morphisme de groupes, et elle est facile à calculer pour un cycle.

In [ ]:
def signature_cycle(c):
    return (-1) ** (len(c) + 1)

La signature d'une permutation quelconque s'en déduit.

In [ ]:
def signature(s):
    cs = vers_cycles(s)
    p = 1
    for c in cs:
        p = p * signature_cycle(c)
    return p

In [ ]:
s = random_perm(20)
print(s)
print(signature(s))

La fonction `stats_signature` renvoie une estimation de l'espérance de la signature. Si $n\ge 2$, la valeur exacte de cette espérance est 0. En effet

$$E(\varepsilon)=\frac 1{n!}\sum_{\sigma\in\mathfrak S_n}\varepsilon(\sigma)=\frac 1{n!}(|\mathfrak A_n|-|\mathfrak S_n\setminus\mathfrak A_n|)$$

où $\mathfrak A_n$ est l'ensemble des permutations paires. Or,

$$|\mathfrak A_n|=|\mathfrak S_n\setminus\mathfrak A_n|=\frac 1 2 n!$$

On a donc $E(\varepsilon)=0$.

In [ ]:
def stats_signature(n):
    N = 1000
    av = 0.
    for k in range(N):
        s = random_perm(n)
        av = av + signature(s)
    return av / N

In [ ]:
stats_signature(20)

## 6. Ordre d'une permutation

L'ordre d'une permutation est le ppcm des ordres des cycles qui la composent. Or, l'ordre d'un cycle est sa longueur.

On commence par définir pgcd et ppcm.

In [ ]:
def pgcd(a, b):
    while b != 0: a, b = b, a % b
    return a

In [ ]:
pgcd(18, 28)

In [ ]:
def ppcm(a, b):
    if a == 0 and b == 0: return 0
    else:
        d = pgcd(a, b)
        return (a // d) * b

In [ ]:
ppcm(4, 6)

Maintenant il est facile de calculer l'ordre d'une permutation.

In [ ]:
def ordre(s):
    cs = vers_cycles(s)
    p = 1
    for c in cs:
        p = ppcm(p, len(c))
    return p

Soyons sans peur, testons sur une permutation $s$ de taille 100000. On calcule l'ordre $\omega$ de $s$, puis on vérifie que $s^\omega=id$. Le tout prend moins de 5 secondes sur ma machine (qui n'est pas très rapide). Cela dépend un peu évidemment de la permutation tirée au sort. 

Pour $n = 10^6$, le calcul de l'ordre se fait sur ma machine en 4 ou 5 secondes, la vérification en une trentaine de secondes. 

In [ ]:
n = 100000
s = random_perm(n)
o = ordre(s)
print(o)
print(puissance(s, o) == id(n))

Quel est l'ordre moyen $\mu_n$ d'une permutation de taille $n$ ? Nous admettrons ici que

$$\ln \mu_n\sim c\sqrt{\frac {n}{\ln n}}$$

où 

$$c=2\sqrt{2\int_0^\infty\frac{\ln(1+t)}{e^t-1}\, dt}\simeq 2.99047$$

L'intégrale apparaissant dans la constante est la **contante de Goh et Schmutz**.

Juste histoire de vérifier cette valeur, voici une fonction `trapezes`. Elle renvoie une approximation de $\int_a^bf(x)\,dx$ par la méthode des trapèzes.

In [ ]:
def trapezes(f, a, b, n):
    d = (b - a) / n
    s = 0
    for k in range(n):
        s += f(a + k * d)
    s += (f(b) - f(a)) / 2
    return d * s

Voici la constante de Goh et Schmutz.

In [ ]:
goh_schmutz = trapezes(lambda x:math.log(1 + x) / (math.exp(x) - 1), 0.00001, 100, 10000)
print(goh_schmutz)

Et voici une estimation de la constante $c$ ci-dessus.

In [ ]:
print(2 * math.sqrt(2 * goh_schmutz))

Ne soyons pas trop exigeants dans nos tests. Je cite l'article dans lequel j'ai trouvé ce résultat :

"__It turns out that a small set of exceptional permutations contributes significantly to the value of $\mu_n$__".

L'article en question est *William M. Y. Goh, Eric Scmutz, The expected Order of a Random Permutation, Bull. London  Math. Soc. 23 (1991) 34-42*.

Cauchemar du statisticien, un petit nombre d'individus domine le groupe. Un calcul sur quelques (milliers de) permutations donnera donc un résultat a priori pas bon.

In [ ]:
def stats_ordre(n, N=1000):
    av = 0.
    for k in range(N):
        s = random_perm(n)
        av = av + ordre(s)
    return av / N

In [ ]:
mu = stats_ordre(1000)
print(mu)

In [ ]:
n = 1000
c = 2.99047
print(math.log(mu))
print(c * math.sqrt(n / math.log(n)))

On s'en contentera :-).

Ce n'est évidemment pas la fin de l'histoire, d'autres quantités associées aux permutations se prêtent aussi à des explorations probabilistes très intéressantes (et souvent non triviales).